# Klasyfikacja binarna dla tekstu

Zakładamy, że mamy dwie klasy: $c$ i jej dopełnienie ($\bar{c}$).

Typowym przykładem jest zadanie klasyfikacji mejla, czy należy do spamu, czy nie (_spam_ vs _ham_), czyli innymi słowy filtr antyspamowy.

**Pytanie**: Czy można wyobrazić sobie zadanie klasyfikacji mejli, niebędące zadaniem klasyfikacji binarnej?

Zakładamy paradygmat uczenia nadzorowanego, tzn. dysponujemy zbiorem uczącym.

**Pytanie**: Czym jest i w jaki sposób powstaje zbiór uczący dla filtru antyspamowego?

## Klasyfikacja regułowa

Filtr anyspamowe _można_ zrealizować za pomocą metod innych niż opartych na uczeniu maszynowym. Można np. tworzyć reguły (np. wyrażenia regularne). Przykładem są (barokowe...) reguły w programie SpamAssassin, zob. fragment [pliku reguł](https://github.com/apache/spamassassin/blob/trunk/rules/20_advance_fee.cf):

```
header __FRAUD_VQE	Subject =~ /^(?:Re:|\[.{1,10}\])?\s*(?:very )?urgent\s+(?:(?:and|&)\s+)?(?:confidential|assistance|business|attention|reply|response|help)\b/i

body __FRAUD_DBI	/(?:\bdollars?\b|\busd(?:ollars)?(?:[0-9]|\b)|\bus\$|\$[0-9,.]{6,}|\$[0-9].{0,8}[mb]illion|\$[0-9.,]{2,10} ?m|\beuros?\b|u[.]?s[.]? [0-9.]+ m)/i
body __FRAUD_KJV	/(?:claim|concerning) (?:the|this) money/i
body __FRAUD_IRJ	/(?:finance|holding|securit(?:ies|y)) (?:company|firm|storage house)/i
body __FRAUD_NEB	/(?:government|bank) of nigeria/i
body __FRAUD_XJR	/(?:who was a|as a|an? honest|you being a|to any) foreigner/i
```

**Pytanie:** Jakie są wady i zalety regułowych filtrów antyspamowych?

Współcześnie zdecydowanie dominuje użycie metod statystycznych (opartych na nadzorowanym uczeniu maszynowym). Do popularności tych metod przyczynił się artykuł [Plan for spam](http://www.paulgraham.com/spam.html) autorstwa Paula Grahama.

## Podejście generatywne i dyskryminatywne

W klasyfikacji (i w ogóle w uczeniu nadzorowanym) można wskazać dwa podejścia:

* generatywne - wymyślamy pewną "historyjkę", w jaki sposób powstaje tekst, "historyjka" powinna mieć miejsca do wypełnienia (parametry), np. częstości wyrazów, na podstawie zbioru uczącego dobieramy wartości parametrów (przez rachunki wprost); "historyjka" nie musi być prawdziwa, wystarczy, że jakoś przybliża rzeczywistość

* dyskryminatywne - nie zastanawiamy się, w jaki sposób powstają teksty, po prostu "na siłę" dobieramy wartości parametrów (wag) modelu, tak aby uzyskać jak najmniejszą wartość funkcji kosztu na zbiorze uczącym; zwykle odbywa się to w iteracyjnym procesie (tak jak przedstawiono na schemacie na poprzednim wykładzie).

**Pytanie**: Jakie są wady i zalety obu podejść?

## Nasz "dyżurny" przykład

Zakładamy, że nasz zbiór uczący ($X$) składa się z 4 dokumentów:

* $x_1=\mathit{kup\ pan\ Viagrę}$
* $x_2=\mathit{tanie\ miejsce\ dla\ pana}$
* $x_3=\mathit{viagra\ viagra\ viagra}$
* $x_4=\mathit{kup\ tanie\ cartridge'e}$

z następującymi etykietami:

* $y_1=c$ (spam)
* $y_2=\bar{c}$ (nie-spam)
* $y_3=c$
* $y_4=c$

Zakładamy, że dokumenty podlegają lematyzacji i sprowadzeniu do mały liter, więc ostatecznie będziemy mieli następujące ciąg termów:

* $x_1=(\mathit{kupić}, \mathit{pan}, \mathit{viagra})$
* $x_2=(\mathit{tani}, \mathit{miejsce}, \mathit{dla}, \mathit{pan})$
* $x_3=(\mathit{viagra}, \mathit{viagra}, \mathit{viagra})$
* $x_4=(\mathit{kupić}, \mathit{tani}, \mathit{cartridge})$

$P(tani|c) = (1+1)/(9+7) = 2/16 = 0.125$
$P(viagra|c) = \frac{4+1}{9 + 7} = 5/16 = 0.3125 $
$P(dla|c) = \frac{0+1}{9+7} = 1/16 = 0.0625$
$P(pan|c) = (1+1)/(9+7) = 2/16 = 0.125 $
$P(c) = 0.75$

w wersji wielomianowej: $P(c)P(tani|c)P(tani|c)P(viagra|c)P(dla|c)P(pan|c) = 0.75 * 0.125 * 0.125 * 0.3125 * 0.0625 * 0.125= 0.0002861$

w werjis Bernoulliego: $P(c)P(U_{dla}=1|c)P(U_{cartridge}=0|c)P(U_{viagra}=1|c)P(U_{pan}=1|c)P(U_{tani}=1|c)P(U_{miejsce}=0|c)P(U_{kup}=0|c)$

$P(tani|\bar{c}) = (1+1)/(4+7) = 2/11 =0.182 $
$P(viagra|\bar{c}) = 1/11 = 0.091  $
$P(dla|\bar{c}) = 2/11 = 0.182 $
$P(pan|\bar{c}) = 2/11 = 0.182 $
$P(\bar{c}) = 0.25$

$P(\bar{c})P(tani|\bar{c})P(tani|\bar{c})P(dla|\bar{c})P(pan|\bar{c}) = 0.25 * 0.182 * 0.182 * 0.091 * 0.182 * 0.182 = 0.00002496$



Uczymy na tym zbiorze klasyfikator, który będziemy testować na dokumencie $d=\mathit{tania\ tania\ viagra\ dla\ pana}$, tj. po normalizacji
$d=(\mathit{tani}, \mathit{tani}, \mathit{viagra}, \mathit{dla}, \mathit{pan})$.

**Uwaga:** Przykład jest oczywiście nierealistyczny i trudno będzie nam ocenić sensowność odpowiedzi. Za to będziemy w stanie policzyć ręcznie wynik.


## Naiwny klasyfikator bayesowski

* _naiwny_ - niekoniecznie oznacza, że to "głupi", bezużyteczny klasyfikator
* _klasyfikator_ 
* _bayesowski_ - będzie odwoływać się do wzoru Bayesa.

Naiwny klasyfikator bayesowski raczej nie powinien być stosowany "produkcyjnie" (są lepsze metody). Natomiast jest to metoda bardzo prosta w implementacji dająca przyzwoity _baseline_.

Naiwny klasyfikator bayesowski ma dwie odmiany:

* wielomianową,
* Bernoulliego.

Wielomianowy naiwny klasyfikator bayesowski jest częściej spotykany i od niego zaczniemy.

Mamy dokument $d$ i dwie klasy $c$ i $\bar{c}$. Policzymy prawdopodobieństwa $P(c|d)$ (mamy dokument $d$, jakie jest prawdopodobieństwo, że to klasa $c$) i $P(\bar{c}|d)$. A właściwie będziemy te prawdopodobieństwa porównywać.

**Uwaga**: nasz zapis to skrót notacyjny, właściwie powinniśmy podać zmienne losowe $P(C=c|D=d)$, ale zazwyczaj będziemy je pomijać. 

**Pytanie**: kiedy ostatecznie nasz klasyfikator zwróci informację, że klasa $c$, a kiedy że $\bar{c}$? czy użytkownika interesują prawdopodobieństwa $P(c|d)$ i $P(\bar{c}|d)$?

Zastosujmy najpierw wzór Bayesa.

$P(c|d) = \frac{P(d|c) P(c)}{P(d)}$

$P(\bar{c}|d) = \frac{P(d|\bar{c}) P(\bar{c})}{P(d)}$

(Oczywiście skądinąd $P(\bar{c}|d) = 1 - P(c|d)$, ale nie będziemy teraz tego wykorzystywali.)

Co możemy pominąć, jeśli tylko porównujemy $P(c|d)$ i $P(\bar{c}|d)$?

Użyjmy znaku proporcjonalności $\propto$:

$P(c|d) = \frac{P(d|c) P(c)}{P(d)} \propto P(d|c) P(c)$

$P(\bar{c}|d) = \frac{P(d|\bar{c}) P(\bar{c})}{P(d)} \propto P(d|\bar{c}) P(\bar{c})$

**Pytanie:** czy iloczyn $P(d|c)P(c)$ można interpretować jako prawdopodobieństwo?

#### Prawdopodobieństwo _a priori_

$P(c)$ - prawdopodobieństwo a priori klasy $c$

$\hat{P}(c) = \frac{N_c}{N}$

gdzie

* N - liczba wszystkich dokumentów w zbiorze uczącym
* N_c - liczba dokumentow w zbiorze uczącym z klasą $c$

$\hat{P}(c) = 0,75$

$\hat{P}(\bar{c}) = 0,25$


#### Prawdopodobieństwo _a posteriori_

Jak interpretować $P(d|c)$?

Wymyślmy sobie model generatywny, $P(d|c)$ będzie prawdopodobieństwem, że spamer (jeśli $c$ to spam) wygeneruje tekst.

Załóżmy, że dokument $d$ to ciąg $n$ termów, $d = (t_1\dots t_n)$. Na razie niewiele z tego wynika.

$P(d|c) = P(t_1\dots t_n|c)$

Żeby pójść dalej musimy doszczegółowić nasz model generatywny. Przyjmijmy bardzo naiwny i niezgodny z rzeczywistością model spamera (i nie-spamera): spamer wyciąga wyrazy z worka i wrzuca je z powrotem (losowanie ze zwracaniem). Jedyne co odróżnia spamera i nie-spamera, to **prawdopodobieństwo wylosowania wyrazu** (np. spamer wylosuje słowo _Viagra_ z dość dużym prawdopodobieństwem, nie-spamer - z bardzo niskim).

**Pytanie:** Ile może wynosić $P(\mathit{Viagra}|c)$?

Po przyjęciu takich "naiwnych założeń":

$$P(d|c) = P(t_1\dots t_n|c) \approx P(t_1|c)\dots P(t_n|c) = \prod_i^n P(t_i|c)$$

Jak oszacować $\hat{P}(t|c)$?

$$\hat{P}(t|c) = \frac{\#(t,c)}{\sum_i^{|V|} \#(t_i,c)} = \frac{\mathit{ile\ razy\ term\ t\ pojawił\ się\ w\ dokumentach\ klasy\ c}}{liczba\ wyrazów\ w\ klasie\ c}$$

### Wygładzanie

Mamy problem z zerowymi prawdopodobieństwami.

Czy jeśli w naszym zbiorze uczącym spamerzy ani razu nie użyli słowa _wykładzina_, to $P(\mathit{wykładzina}|c) = 0$?.

Musimy zastosować wygładzanie (_smoothing_). Spróbujmy wymyślić wygładzanie wychodząc od zdroworozsądkowych aksjomatów.

#### Aksjomaty wygładzania.

Założmy, że mamy dyskretną przestrzeń probabilistyczną $\Omega = \{\omega_1,\dots,\omega_m\}$, zdarzenie $\omega_i$ w naszym zbiorze uczącym wystąpiło $k_i$ razy. Wprost prawdopodobieństwa byśmy oszacowali tak: $P(\omega_i) = \frac{k_i}{\sum_j^m k_j}$.
Szukamy zamiast tego funkcji wygładzającej $f(m, k, T)$ (innej niż $f(m, k, T) = \frac{k}{T}$), która spełniałaby następujące aksjomaty:

1. $f(m, k, T) \in [0, 1]$
2. $f(m, k, T) \in (0, 1)$ jeśli $m > 1$
3. $\sum_i f(m, k_i, T) = 1$, jeśli $\sum_i k_i = T$
4. $f(m, 0, 0) = \frac{1}{m}$
5. $\lim_{T \to \inf} f(m, k, T) = \frac{k}{T}$


m=2, k1=2, k2=4, T=6, 2/6 => f(2, 2, 6) > 0.333,  f(2, 4, 6) < 0.666 

Jaka funkcja spełnia te aksjomaty?

$$f(m, k, T) = \frac{k+1}{T+m}$$

Jest to wygładzanie +1, albo wygładzanie Laplace'a.

**Pytanie:** Wymyślić jakiś inny przykład funkcji, która będzie spełniała aksjomaty.








Po zastosowaniu do naszego naiwnego klasyfikatora otrzymamy:
    
$$\hat{P}(t|c) = \frac{\#(t,c) + 1}{\sum_i^{|V|} \#(t_i,c) + |V|}$$

### Metoda Bernoulliego

$$P(𝑑|𝑐) \approx P(U=u_1|c)\dots P(U=u_{|v|})$$, gdzie $u_i = 1$, $t_i$ pojawił się w dokumencie $d$, 0 - w przeciwnym razie



$\hat{P}(U_{viagra}=1|c) = \frac{\#(viagra,N_c) + 1}{N_c + 2}$